In [6]:
# !pip install folium

In [7]:
import pandas as pd
import numpy as np
import requests
from IPython.display import HTML, display
from bs4 import BeautifulSoup
from bs4 import Comment
import json
import html
import re
import urllib.parse
from datetime import datetime
import threading
lock = threading.RLock()
from os import walk

datasets_names = []
path_df = '../datasets/original_files/'
for (dirpath, dirnames, filenames) in walk(path_df):
    datasets_names.extend(filenames)
    break
dataFrame = False
first = True
for name in datasets_names:
    if(first):
        first = False
        dataFrame = pd.read_csv(path_df+name, compression='gzip')
        dataFrame.set_index('id', drop=False, inplace=True)
        print('adding', len(dataFrame), 'rows')
    else:
        _tmpDf = pd.read_csv(path_df+name, compression='gzip')
        _tmpDf.set_index('id', drop=False, inplace=True)
        print('adding', len(_tmpDf), 'rows')
        dataFrame = pd.concat([dataFrame, _tmpDf])
        del _tmpDf
dataFrame.loc[:,  'price'] = dataFrame.price.apply(lambda x: x[1:-3].replace(',', '')).astype(int)
print('total rows:', len(dataFrame))
dataFrame.head()

C:\ProgramData\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3020: DtypeWarning: Columns (61,62) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


adding 11668 rows
adding 3799 rows
adding 4868 rows
adding 38481 rows
adding 7211 rows


C:\ProgramData\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3020: DtypeWarning: Columns (61,62,94) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


adding 50796 rows


C:\ProgramData\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3020: DtypeWarning: Columns (43,94) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


adding 13927 rows
total rows: 130750


id                        listing_url       scrape_id last_scraped  \
id                                                                           
2265  2265  https://www.airbnb.com/rooms/2265  20200317143754   2020-03-17   
5245  5245  https://www.airbnb.com/rooms/5245  20200317143754   2020-03-17   
5456  5456  https://www.airbnb.com/rooms/5456  20200317143754   2020-03-17   
5769  5769  https://www.airbnb.com/rooms/5769  20200317143754   2020-03-17   
6413  6413  https://www.airbnb.com/rooms/6413  20200317143754   2020-03-17   

                                                   name  \
id                                                        
2265   Zen-East in the Heart of Austin (monthly rental)   
5245  Eco friendly, Colorful, Clean, Cozy monthly share   
5456          Walk to 6th, Rainey St and Convention Ctr   
5769                                     NW Austin Room   
6413                      Gem of a Studio near Downtown   

                                                summary  \
id                                                        
2265  Zen East is situated in a vibrant & diverse mu...   
5245  Situated in a vibrant & diverse multicultural ...   
5456  Great central  location for walking to Convent...   
5769                                                NaN   
6413  Great studio apartment, perfect for couples or...   

                                                  space  \
id                                                        
2265  This colorful and clean 1923 house was complet...   
5245  This green, colorful, clean and cozy house was...   
5456  Cute Private Studio apartment located in Willo...   
5769  Looking for a comfortable inexpensive room to ...   
6413  !!!!! SXSW info !!!!! Presently open (again!) ...   

                                            description experiences_offered  \
id                                                                            
2265  Zen East is situated in a vibrant & diverse mu...                none   
5245  Situated in a vibrant & diverse multicultural ...                none   
5456  Great central  location for walking to Convent...                none   
5769  Looking for a comfortable inexpensive room to ...                none   
6413  Great studio apartment, perfect for couples or...                none   

                                  neighborhood_overview        ...          \
id                                                             ...           
2265                                                NaN        ...           
5245                                                NaN        ...           
5456  My neighborhood is ideally located if you want...        ...           
5769  Quiet neighborhood with lots of trees and good...        ...           
6413  Travis Heights is one of the oldest neighborho...        ...           

     instant_bookable is_business_travel_ready          cancellation_policy  \
id                                                                            
2265                f                        f  strict_14_with_grace_period   
5245                f                        f  strict_14_with_grace_period   
5456                f                        f  strict_14_with_grace_period   
5769                f                        f                     moderate   
6413                t                        f  strict_14_with_grace_period   

     require_guest_profile_picture require_guest_phone_verification  \
id                                                                    
2265                             f                                f   
5245                             f                                f   
5456                             f                                t   
5769                             t                                t   
6413                             f                                f   

      calculated_host_listings_count  \
id                        

In [41]:
import folium
from folium.plugins import HeatMap



hmap = folium.Map(location=[40.75, -73.95], zoom_start=11, )

hm_wide = HeatMap(
                    list(zip(
                        dataFrame.latitude.values,
                        dataFrame.longitude.values, 
                        dataFrame.price
                    )),
                    min_opacity=0.01,
                    max_val=30000,
                    radius=7, blur=10, 
                    max_zoom=1,
)

hmap.add_child(hm_wide)